# Clustering based on corelationship

In [2]:
import pdb

In [3]:
with open('./file_funcs.json','r') as f:
    data = json.load(f)

In [14]:
with open('/projects/bdata/jupyter/decision_points/sklearn.txt','r') as f:
    dp = [l for l in f.read().split('\n') if l]

In [4]:
len(data)

87102

In [5]:
from config import nb_path

In [6]:
import os

In [7]:
data["nb_985174.py"]

{'funcs': ['googlemaps.Client',
  'googlemaps.Client.geocode',
  'get_ipython.magic',
  'get_ipython',
  'get',
  'pandas.read_csv'],
 'linenos': [8, 9, 21, 21, 38, 51]}

In [8]:
sklearn_notebooks = []
for file in data:
    for func in data[file]["funcs"]:
        if func.startswith('sklearn.'):
            sklearn_notebooks.append(file)
            break
        

In [9]:
len(sklearn_notebooks)

47760

In [10]:
from tqdm import tqdm

In [42]:
vec_size = 0
window_size = 100
for file in sklearn_notebooks:
    with open(os.path.join(nb_path, file),'r') as f:
        vec_size+=len(f.read().split('\n'))-window_size+1
#         print(file, len(f.read().split('\n')))
print(vec_size)

12758759


In [49]:
c = []
for _ in range(2000):
    c.append(np.zeros((1, vec_size), dtype=int))

In [70]:
from scipy.special import softmax

In [12]:
import numpy as np

In [53]:
func2vector = {}
index=0
cnt = 0
for file in sklearn_notebooks:
#     print('='*20)
#     cnt+=1
    with open(os.path.join(nb_path, file),'r') as f:
        doc_size = len(f.read().split('\n'))
#     print(doc_size-window_size)
    window = []
    window_l = []
#     print(data[file])
    funcs = [i for i in data[file]["funcs"]]
#     print(funcs)
    linenos = [i for i in data[file]["linenos"]]
#     print(len(funcs))
#     pdb.set_trace()
#     print([f for f in funcs if f.startswith('sklearn.')])
#     for i in range(doc_size-window_size):
#     i=0
#     print(linenos)
    i=linenos[0]
    while i<doc_size-window_size:
        while funcs!=[] and linenos[0]<=i+window_size:
            window.append(funcs.pop(0))
#             funcs.
            window_l.append(linenos.pop(0))
        while window!=[] and window_l[0]<=i:
            window.pop(0)
            window_l.pop(0)
#         print('-'*20)
#         print(i)
#         for f in window:
#             if f.startswith('sklearn.'):
#                 print(f)
#         print([f for f in window if f.startswith('sklearn.')])
#         if window!=[]:
#             pdb.set_trace()
        for f in set(window):
            if not (f.startswith('sklearn.') and f in dp):continue
            if f not in func2vector:
                func2vector[f] = np.zeros(vec_size)
            func2vector[f][index]=1
#         print(window_l)
#         print(linenos)

#         print(i)
#         i=window_l[]
        index+=1
        
        if index%100000==0:
            print(index)
        if linenos==[]:
            break
        try:
            i = window_l[0]
        except:
            i = linenos[0]-1
            
#         print(doc_size-window_size)
#         print(i<doc_size-window_size)
#     if cnt==10:
#         break
print(index)

100000
200000
300000
400000
500000
600000
700000
800000
900000
1000000
1100000
1200000
1300000
1400000
1500000
1600000
1700000
1800000
1900000
2000000
2100000
2200000
2300000
2400000
2500000
2600000
2700000
2800000
2900000
2900715


In [56]:
func2vector = {f:func2vector[f][:index] for f in func2vector}

In [58]:
idx2func = list(func2vector.keys())
mat = np.stack([func2vector[f] for f in idx2func], axis = 0)

In [60]:
np.argwhere(mat>1)

array([], shape=(0, 2), dtype=int64)

In [49]:
bi_func2vector = {f:func2vector[f] for f in func2vector}

for f in bi_func2vector:
    bi_func2vector[f][bi_func2vector[f]>1]=1




 12%|█▏        | 505/4249 [00:33<01:36, 38.96it/s]

In [20]:
len(func2vector)


4249

In [28]:
for f in func2vector:
    func2vector[f] = func2vector[f][:index]

In [3]:
func2vector

NameError: name 'func2vector' is not defined

In [22]:
occur_mat = np.stack(list(func2vector.values()), axis=0)

In [51]:
bi_occur_mat = np.stack(list(bi_func2vector.values()), axis=0)

In [52]:
bi_occur_mat

array([[1., 1., 1., ..., 0., 0., 0.],
       [1., 1., 1., ..., 0., 0., 0.],
       [1., 1., 1., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [25]:
cooccur = np.dot(occur_mat, occur_mat.T)

In [54]:
bi_cooccur = np.dot(bi_occur_mat, bi_occur_mat.T)

In [56]:
bi_cooccur.max()

3695442.0

In [63]:
t = np.sqrt(bi_cooccur)

In [27]:
cooccur.shape

(4249, 4249)

In [28]:
dist = 1-cooccur/cooccur.max()

In [57]:
bi_dist = 1-bi_cooccur/bi_cooccur.max()

In [75]:
t = 1-softmax(t,axis=1)

In [98]:
t

array([[0.80011012, 0.80011012, 0.80011012, ..., 0.99999987, 0.99999987,
        0.99999987],
       [0.80011012, 0.80011012, 0.80011012, ..., 0.99999987, 0.99999987,
        0.99999987],
       [1.        , 1.        , 0.5       , ..., 1.        , 1.        ,
        1.        ],
       ...,
       [1.        , 1.        , 1.        , ..., 0.96000001, 0.96000001,
        1.        ],
       [1.        , 1.        , 1.        , ..., 0.96000001, 0.96000001,
        1.        ],
       [1.        , 1.        , 1.        , ..., 1.        , 1.        ,
        0.97777778]])

In [61]:
from sklearn import cluster

In [79]:
model = cluster.AgglomerativeClustering(n_clusters = None, distance_threshold=0.95, affinity="precomputed", linkage="average").fit(t)

In [80]:
model.n_clusters_

3346

In [82]:
idx2func =list( bi_func2vector.keys())

In [83]:
new_clusters = {}
# new_clusters = [[]]*model.n_clusters_
for i, l in enumerate(model.labels_):
    if l not in new_clusters:
        new_clusters[l] = []
    new_clusters[l].append(idx2func[i])
#     print(i)
clusters = list(new_clusters.values())

In [85]:
for c in clusters:
    print('-'*20)
    for f in c:
        print(f)
#     print(c)

--------------------
sklearn.feature_extraction.text.TfidfVectorizer.transform.multiply
sklearn.feature_extraction.text.TfidfVectorizer.transform.multiply.sum
sklearn.feature_extraction.text.TfidfVectorizer.transform
sklearn.feature_extraction.text.TfidfVectorizer.fit
sklearn.feature_extraction.text.TfidfVectorizer
--------------------
sklearn.cross_validation.cross_val_score
--------------------
sklearn.linear_model.LogisticRegression
--------------------
sklearn.feature_extraction.text.CountVectorizer.transform
sklearn.feature_extraction.text.CountVectorizer.fit
sklearn.feature_extraction.text.CountVectorizer
--------------------
sklearn.svm.SVC.fit.predict
sklearn.svm.SVC
--------------------
sklearn.svm.SVC.fit
--------------------
sklearn.linear_model.Lasso.score
sklearn.linear_model.Lasso.predict
sklearn.linear_model.Lasso.fit
sklearn.linear_model.Lasso
--------------------
sklearn.metrics.mean_squared_error
--------------------
sklearn.linear_model.Ridge.score
sklearn.linear_mod

--------------------
sklearn.model_selection.cross_val_score.max
--------------------
sklearn.decomposition.PCA.fit.components_.transpose
--------------------
sklearn.metrics.homogeneity_completeness_v_measure
--------------------
sklearn.svm.SVC.coef_.todense
--------------------
sklearn.ensemble.BaggingClassifier.score
--------------------
sklearn.ensemble.ExtraTreesClassifier.fit.fit.predict
--------------------
sklearn.preprocessing.FunctionTransformer.transform
--------------------
sklearn.feature_extraction.text.CountVectorizer.vocabulary_.items
--------------------
sklearn.linear_model.LogisticRegression.predict.flatten
sklearn.linear_model.LogisticRegression.predict.flatten.astype
--------------------
sklearn.svm.LinearSVC.fit.fit
--------------------
sklearn.ensemble.VotingClassifier.fit.fit
--------------------
sklearn.linear_model.BayesianRidge.score
sklearn.linear_model.BayesianRidge.fit
sklearn.linear_model.BayesianRidge
--------------------
sklearn.preprocessing.scale.std

sklearn.linear_model.logistic.LogisticRegression.score
--------------------
sklearn.externals.joblib.load.toarray
--------------------
sklearn.metrics.confusion_matrix.trace
--------------------
sklearn.svm.LinearSVC.LinearSVC
--------------------
sklearn.ensemble.RandomForestClassifier.predict.reshape.astype.astype
sklearn.ensemble.RandomForestClassifier.predict.reshape
--------------------
sklearn.datasets.load_boston.head
--------------------
sklearn.tree.DecisionTreeClassifier.feature_importances_.tolist
--------------------
sklearn.preprocessing.PolynomialFeatures.fit_transform.all
--------------------
sklearn.preprocessing.scale.all
--------------------
sklearn.cluster.DBSCAN.fit.get_params
--------------------
sklearn.metrics.silhouette_samples.sort_values
--------------------
sklearn.ensemble.IsolationForest.fit.predict
--------------------
sklearn.pipeline.Pipeline.predict.min
--------------------
sklearn.pipeline.Pipeline.source_predict
--------------------
sklearn.linear_mod

--------------------
sklearn.preprocessing.MultiLabelBinarizer.fit.inverse_transform
sklearn.preprocessing.MultiLabelBinarizer.fit.transform.astype.astype
sklearn.preprocessing.MultiLabelBinarizer.fit.transform.append
--------------------
sklearn.feature_selection.mutual_info_classif.argsort
--------------------
sklearn.linear_model.LogisticRegression.coef_.transpose
--------------------
sklearn.mixture.gmm.GMM.score
sklearn.mixture.gmm.GMM.fit
sklearn.mixture.gmm.GMM
sklearn.naive_bayes.GaussianNB.fit._joint_log_likelihood
--------------------
sklearn.preprocessing.StandardScaler.fit_transform.ravel
--------------------
sklearn.pipeline.Pipeline.transform.drop
sklearn.feature_selection.RFE.fit.transform
--------------------
sklearn.pipeline.Pipeline.transform.apply
sklearn.feature_selection.RFE.fit.transform.apply
--------------------
sklearn.linear_model.Lasso.coef_.tolist.append
--------------------
sklearn.metrics.classification.log_loss
--------------------
sklearn.ensemble.Gradie

In [87]:
idx2func = [f for f in bi_func2vector if f in dp]
mat = np.stack([bi_func2vector[f] for f in idx2func], axis = 0)

In [89]:
idx2func[0]

'sklearn.feature_extraction.text.TfidfVectorizer'

In [90]:
mat.shape

(389, 15109804)

In [62]:
co_mat = np.dot(mat,mat.T)

In [63]:
co_mat

array([[4.46250e+04, 8.38000e+02, 6.04200e+03, ..., 0.00000e+00,
        0.00000e+00, 0.00000e+00],
       [8.38000e+02, 6.54980e+04, 5.72800e+03, ..., 0.00000e+00,
        0.00000e+00, 0.00000e+00],
       [6.04200e+03, 5.72800e+03, 1.98733e+05, ..., 0.00000e+00,
        0.00000e+00, 0.00000e+00],
       ...,
       [0.00000e+00, 0.00000e+00, 0.00000e+00, ..., 8.00000e+00,
        0.00000e+00, 0.00000e+00],
       [0.00000e+00, 0.00000e+00, 0.00000e+00, ..., 0.00000e+00,
        9.00000e+00, 0.00000e+00],
       [0.00000e+00, 0.00000e+00, 0.00000e+00, ..., 0.00000e+00,
        0.00000e+00, 1.00000e+01]])

In [64]:
np.sqrt(co_mat)

array([[211.24630174,  28.94822965,  77.73030297, ...,   0.        ,
          0.        ,   0.        ],
       [ 28.94822965, 255.92577049,  75.68355171, ...,   0.        ,
          0.        ,   0.        ],
       [ 77.73030297,  75.68355171, 445.79479584, ...,   0.        ,
          0.        ,   0.        ],
       ...,
       [  0.        ,   0.        ,   0.        , ...,   2.82842712,
          0.        ,   0.        ],
       [  0.        ,   0.        ,   0.        , ...,   0.        ,
          3.        ,   0.        ],
       [  0.        ,   0.        ,   0.        , ...,   0.        ,
          0.        ,   3.16227766]])

In [65]:
nt = np.sqrt(co_mat)

In [66]:
nt

array([[211.24630174,  28.94822965,  77.73030297, ...,   0.        ,
          0.        ,   0.        ],
       [ 28.94822965, 255.92577049,  75.68355171, ...,   0.        ,
          0.        ,   0.        ],
       [ 77.73030297,  75.68355171, 445.79479584, ...,   0.        ,
          0.        ,   0.        ],
       ...,
       [  0.        ,   0.        ,   0.        , ...,   2.82842712,
          0.        ,   0.        ],
       [  0.        ,   0.        ,   0.        , ...,   0.        ,
          3.        ,   0.        ],
       [  0.        ,   0.        ,   0.        , ...,   0.        ,
          0.        ,   3.16227766]])

In [71]:
softmax(nt, axis=1)

array([[1.00000000e+000, 6.74455390e-080, 1.03451904e-058, ...,
        1.80674487e-092, 1.80674487e-092, 1.80674487e-092],
       [2.66015228e-099, 1.00000000e+000, 5.26985882e-079, ...,
        7.12607026e-112, 7.12607026e-112, 7.12607026e-112],
       [1.41782217e-160, 1.83117135e-161, 1.00000000e+000, ...,
        2.47616799e-194, 2.47616799e-194, 2.47616799e-194],
       ...,
       [2.48188947e-003, 2.48188947e-003, 2.48188947e-003, ...,
        4.19906628e-002, 2.48188947e-003, 2.48188947e-003],
       [2.26562991e-003, 2.26562991e-003, 2.26562991e-003, ...,
        2.26562991e-003, 4.55063932e-002, 2.26562991e-003],
       [2.44126116e-003, 2.44126116e-003, 2.44126116e-003, ...,
        2.44126116e-003, 2.44126116e-003, 5.76731909e-002]])

In [72]:
na = 1-nt/nt.max(axis = 1)

In [73]:
na

array([[0.        , 0.88688818, 0.82563659, ..., 1.        , 1.        ,
        1.        ],
       [0.86296456, 0.        , 0.83022783, ..., 1.        , 1.        ,
        1.        ],
       [0.63203946, 0.70427538, 0.        , ..., 1.        , 1.        ,
        1.        ],
       ...,
       [1.        , 1.        , 1.        , ..., 0.        , 1.        ,
        1.        ],
       [1.        , 1.        , 1.        , ..., 1.        , 0.        ,
        1.        ],
       [1.        , 1.        , 1.        , ..., 1.        , 1.        ,
        0.        ]])

In [138]:
na

array([[0.52730839, 0.76261873, 0.69224908, ..., 1.        , 1.        ,
        1.        ],
       [0.76261873, 0.        , 0.73455735, ..., 1.        , 1.        ,
        1.        ],
       [0.69224908, 0.73455735, 0.50022668, ..., 1.        , 0.99257728,
        1.        ],
       ...,
       [1.        , 1.        , 1.        , ..., 0.99166246, 1.        ,
        1.        ],
       [1.        , 1.        , 0.99257728, ..., 1.        , 0.99257728,
        1.        ],
       [1.        , 1.        , 1.        , ..., 1.        , 1.        ,
        0.99403932]])

In [105]:
model = cluster.AgglomerativeClustering(n_clusters = None, distance_threshold=0.5, affinity="precomputed", linkage="average").fit(na)

In [106]:
model.n_clusters_

200

In [107]:
new_clusters = {}
# new_clusters = [[]]*model.n_clusters_
for i, l in enumerate(model.labels_):
    if l not in new_clusters:
        new_clusters[l] = []
    new_clusters[l].append(idx2func[i])
#     print(i)
clusters = list(new_clusters.values())

In [108]:
for c in clusters:
    print('-'*20)
    for f in c:
        print(f)
#     print(c)

--------------------
sklearn.feature_extraction.text.TfidfVectorizer
sklearn.feature_selection.univariate_selection.SelectKBest
--------------------
sklearn.preprocessing.LabelEncoder
sklearn.semi_supervised.LabelSpreading
--------------------
sklearn.linear_model.LogisticRegression
sklearn.datasets.load_iris
sklearn.svm.l1_min_c
--------------------
sklearn.metrics.mean_squared_error
sklearn.metrics.mean_absolute_error
sklearn.metrics.median_absolute_error
sklearn.metrics.r2_score
sklearn.linear_model.MultiTaskElasticNet
sklearn.metrics.explained_variance_score
--------------------
sklearn.metrics.confusion_matrix
sklearn.tree.export_graphviz
sklearn.tree.tree.DecisionTreeClassifier
--------------------
sklearn.metrics.classification_report
sklearn.datasets.fetch_20newsgroups
sklearn.datasets.twenty_newsgroups.strip_newsgroup_footer
sklearn.datasets.twenty_newsgroups.strip_newsgroup_quoting
--------------------
sklearn.linear_model.Ridge
sklearn.ensemble.BaggingRegressor
sklearn.linea

In [74]:
1-t/t.max()

array([[0.99258835, 0.99258835, 0.99258835, ..., 1.        , 1.        ,
        1.        ],
       [0.99258835, 0.99258835, 0.99258835, ..., 1.        , 1.        ,
        1.        ],
       [0.99258835, 0.99258835, 0.72537211, ..., 1.        , 1.        ,
        1.        ],
       ...,
       [1.        , 1.        , 1.        , ..., 0.98930115, 0.98930115,
        1.        ],
       [1.        , 1.        , 1.        , ..., 0.98930115, 0.98930115,
        1.        ],
       [1.        , 1.        , 1.        , ..., 1.        , 1.        ,
        0.98116489]])

In [37]:
cooccur/np.sqrt(index)

array([[5.22235779e-02, 5.22235779e-02, 1.56670734e-01, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [5.22235779e-02, 5.22235779e-02, 1.56670734e-01, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [1.56670734e-01, 1.56670734e-01, 1.11669728e+03, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       ...,
       [0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
        1.08820559e-01, 1.08820559e-01, 0.00000000e+00],
       [0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
        1.08820559e-01, 1.08820559e-01, 0.00000000e+00],
       [0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
        0.00000000e+00, 0.00000000e+00, 3.37266555e-01]])

In [38]:
index

15109804

In [39]:
occur_mat.shape

(4249, 15109804)

In [40]:
np.argmax(cooccur)

182750

In [41]:
np.argwhere(cooccur==16300494896.0)

array([[43, 43]])

In [44]:
np.dot(occur_mat[43], occur_mat[43].T)

16300494896.0

In [45]:
np.argwhere(occur_mat[43]>1)

array([[    5977],
       [    5978],
       [    5979],
       ...,
       [15108604],
       [15108605],
       [15108606]])

In [30]:
(cooccur.max())

16300494896.0

In [31]:
from scipy.special import softmax

In [29]:
dist

array([[0.99999999, 0.99999999, 0.99999996, ..., 1.        , 1.        ,
        1.        ],
       [0.99999999, 0.99999999, 0.99999996, ..., 1.        , 1.        ,
        1.        ],
       [0.99999996, 0.99999996, 0.9997337 , ..., 1.        , 1.        ,
        1.        ],
       ...,
       [1.        , 1.        , 1.        , ..., 0.99999997, 0.99999997,
        1.        ],
       [1.        , 1.        , 1.        , ..., 0.99999997, 0.99999997,
        1.        ],
       [1.        , 1.        , 1.        , ..., 1.        , 1.        ,
        0.99999992]])

In [33]:
softmax(cooccur)

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [23]:
idx2func = list(func2vector.keys())
func2idx = {f:i for i,f in enumerate(idx2func)}

In [21]:
corelation_mat = np.zeros((len(idx2func), len(idx2func)))

In [25]:
for i in tqdm(range(len(idx2func))):
    for j in range(i, len(idx2func)):
        corelation_mat[i][j] = np.inner(func2vector[idx2func[i]], func2vector[idx2func[j]])
        if i!=j:
            corelation_mat[j][i] = corelation_mat[i][j]

  2%|▏         | 99/4249 [03:26<1:57:58,  1.71s/it]

KeyboardInterrupt: 

# Calculate top n instead of clustering 

In [3]:
from utils import split_func_name
import numpy as np
import random
import scipy
from scipy import *
import scipy.spatial
import sklearn.metrics
import xgboost
from sklearn import cluster
import statsmodels
import keras
import gensim

In [9]:
LIB = gensim

In [10]:
with open('/projects/bdata/jupyter/decision_points/{}.txt'.format(LIB.__name__),'r') as f:
    dp = f.read().split('\n')
    dp = [l for l in dp if l]

In [13]:
vocab = []
for f in dp:
    tokens = split_func_name(f)
    for t in tokens:
        if t not in vocab:
            vocab.append(t)
w2i = {w:i for i, w in enumerate(vocab)}

In [16]:
func2vector = {}
for f in dp:
    func2vector[f] = np.zeros(len(vocab))
    tokens = split_func_name(f)
    for i, t in enumerate(tokens):
        func2vector[f][w2i[t]]=1*i/len(tokens)

In [17]:
vectors = np.stack([func2vector[f] for f in dp])

In [18]:
sim_mat = sklearn.metrics.pairwise.cosine_similarity(vectors)

In [20]:
sorted_mat = np.argsort(sim_mat, axis = 1)

In [21]:
sorted_mat[:,-10:]

array([[108,   3,   4, ...,   5,  12,   0],
       [ 10,   8,   6, ...,   2,  13,   1],
       [ 10,   8,   6, ...,   1,  13,   2],
       ...,
       [106, 108, 107, ..., 112, 118, 117],
       [106, 108, 107, ..., 112, 117, 118],
       [106, 108, 107, ..., 118, 117, 119]])

In [22]:
dist = 1-sim_mat

In [24]:
model = cluster.AgglomerativeClustering(n_clusters = None, distance_threshold=0.85, affinity="precomputed", linkage="average").fit(dist)

In [25]:
model.n_clusters_

24

In [26]:
new_clusters = {}
for i, l in enumerate(model.labels_):
    if l not in new_clusters:
        new_clusters[l] = []
    new_clusters[l].append(dp[i])
clusters = list(new_clusters.values())

In [28]:
for c in clusters:
    print('\n')
    for f in c:
        print(f)



gensim.corpora.BleiCorpus
gensim.corpora.IndexedCorpus
gensim.corpora.LowCorpus
gensim.corpora.MalletCorpus
gensim.corpora.MmCorpus
gensim.corpora.SvmLightCorpus
gensim.corpora.TextCorpus
gensim.corpora.TextDirectoryCorpus
gensim.corpora.UciCorpus
gensim.corpora.WikiCorpus
gensim.corpora.bleicorpus.BleiCorpus
gensim.corpora.mmcorpus.MmCorpus
gensim.corpora.ucicorpus.UciCorpus
gensim.corpora.wikicorpus.WikiCorpus
gensim.matutils.Dense2Corpus
gensim.matutils.Scipy2Corpus
gensim.matutils.Sparse2Corpus
gensim.matutils.corpus2csc
gensim.matutils.corpus2dense
gensim.models.word2vec.Text8Corpus
gensim.utils.ClippedCorpus
gensim.utils.SlicedCorpus


gensim.corpora.Dictionary
gensim.corpora.HashDictionary
gensim.corpora.dictionary.Dictionary


gensim.matutils.any2sparse
gensim.matutils.sparse2full
gensim.models.Doc2Vec
gensim.models.Word2Vec
gensim.models.atmodel.construct_author2doc
gensim.models.atmodel.construct_doc2author
gensim.models.doc2vec.Doc2Vec
gensim.models.doc2vec.TaggedDocument


# clustering based on cooccurrence (ineffective) 

In [49]:
with open('./file_funcs.json','r') as f:
    data = json.load(f)

In [50]:
f_map = {}
for file in data:
    for f in data[file]['funcs']:
        if not f.startswith('{}.'.format(LIB.__name__)): continue
        for r in dp:
            if f.startswith(r):
                f_map[f] = r
                break

In [53]:
func2vector = {}
vector_size = len(data)
files = list(data.keys())
err_files = []
sklearn_counter = {}
for i, nb in enumerate(files):
    if i%10000 == 0:
        print('Log: {} notebooks processed'.format(i))
    funcs = []
    if nb in data:
        funcs = data[nb]["funcs"]
        linenos = data[nb]["linenos"]
    funcs = [f_map[func] for func in funcs if func in f_map]
    for func in funcs:
        if func not in func2vector:
            func2vector[func] = np.full((vector_size), 0.01)
        if func not in sklearn_counter:
            sklearn_counter[func]=0
        func2vector[func][i] += 1
        sklearn_counter[func]+=1

Log: 0 notebooks processed
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.stats.rv_discrete
scipy.stats.rv_discrete
scipy.stats.rv_discrete
scipy.stats.rv_discrete
--------------------
--------------------
--------------------
scipy.stats.skew
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.optimize.brent
--------------------
--------------------
--------------------
--------------------
scipy.optimize.fmin
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------


--------------------
scipy.stats.spearmanr
scipy.stats.spearmanr
scipy.stats.spearmanr
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.linregress
scipy.stats.spearmanr
scipy.stats.spearmanr
scipy.stats.spearmanr
scipy.stats.spearmanr
scipy.stats.spearmanr
scipy.stats.spearmanr
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.integrate.ode
--------------------
scipy.stats.pearsonr
--------------------
--------------------
--------------------

--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.stats.linregress
scipy.stats.linregress
--------------------
--------------------
--------------------
scipy.stats.spearmanr
scipy.stats.spearmanr
scipy.stats.spearmanr
--------------------
--------------------
--------------------
--------------------
scipy.cluster.hierarchy.linkage
scipy.cluster.hierarchy.dendrogram
scipy.cluster.hierarchy.dendrogram
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.stats.spearmanr
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.sparse.lil_matrix
--------------------
--------------------
-----

--------------------
--------------------
--------------------
scipy.io.loadmat
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.integrate.quad
scipy.integrate.quad
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.sparse.csr_matrix
--------------------
scipy.stats.chisquare
scipy.stats.chi2_contingency
--------------------
--------------------
scipy.stats.pearsonr
scipy.stats.pearsonr
--------------------
--------------------
scipy.stats.linregress
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
---

--------------------
--------------------
--------------------
scipy.sparse.rand
scipy.sparse.rand
scipy.sparse.rand
scipy.sparse.rand
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.stats.spearmanr
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.integrate.quad
--------------------
--------------------
scipy.stats.distributions.entropy
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
-----------

...

scipy.optimize.curve_fit
scipy.optimize.curve_fit
scipy.optimize.curve_fit
scipy.optimize.curve_fit
scipy.optimize.curve_fit
scipy.optimize.curve_fit
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.sparse.csr_matrix
scipy.sparse.csr_matrix
scipy.sparse.lil_matrix
scipy.sparse.lil_matrix
scipy.sparse.lil_matrix
--------------------
scipy.cluster.hierarchy.linkage
scipy.cluster.hierarchy.cophenet
scipy.cluster.hierarchy.dendrogram
scipy.cluster.hierarchy.dendrogram
scipy.cluster.hierarchy.fcluster
--------------------
--------------------
scipy.optimize.least_squares
scipy.optimize.least_squares
scipy.optimize.minimize
scipy.optimize.minimize
--------------------
scipy.cluster.hierarchy.linkage
scipy.cluster.hierarchy.dendrogram
--------------------
--------------------
--------------------
-----------

scipy.cluster.hierarchy.linkage
scipy.cluster.hierarchy.dendrogram
scipy.cluster.hierarchy.linkage
scipy.cluster.hierarchy.dendrogram
scipy.cluster.hierarchy.linkage
scipy.cluster.hierarchy.dendrogram
scipy.cluster.hierarchy.linkage
scipy.cluster.hierarchy.dendrogram
scipy.cluster.hierarchy.linkage
scipy.cluster.hierarchy.dendrogram
scipy.cluster.hierarchy.linkage
scipy.cluster.hierarchy.dendrogram
scipy.cluster.hierarchy.linkage
scipy.cluster.hierarchy.dendrogram
scipy.cluster.hierarchy.linkage
scipy.cluster.hierarchy.dendrogram
scipy.cluster.hierarchy.linkage
scipy.cluster.hierarchy.dendrogram
scipy.cluster.hierarchy.linkage
scipy.cluster.hierarchy.dendrogram
scipy.cluster.hierarchy.linkage
scipy.cluster.hierarchy.dendrogram
scipy.cluster.hierarchy.linkage
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------


scipy.io.savemat
scipy.io.loadmat
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.sparse.csr_matrix
scipy.sparse.hstack
scipy.sparse.csr_matrix
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.linalg.det
scipy.linalg.lu
scipy.linalg.eig
scipy.linalg.solve
scipy.sparse.lil_matrix
scipy.sparse.lil_matrix
scipy.sparse.lil_matrix
scipy.sparse.lil_matrix
--------------------
scipy.stats.sem
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.stats.pearsonr
scipy.stats.pearsonr
scipy.stats.pearsonr
scipy.stats.pearsonr
scipy.stats.pearsonr
scipy.stats.pearsonr
scipy.stats.pearsonr
--------------------
---

--------------------
--------------------
--------------------
--------------------
--------------------
scipy.optimize.newton
scipy.optimize.brent
scipy.optimize.newton
scipy.optimize.newton
--------------------
scipy.linalg.det
scipy.linalg.lu
scipy.linalg.eig
scipy.linalg.solve
scipy.sparse.lil_matrix
scipy.sparse.lil_matrix
scipy.sparse.lil_matrix
scipy.sparse.lil_matrix
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.stats.gaussian_kde
scipy.stats.gaussian_kde
scipy.stats.gaussian_kde
scipy.stats.gaussian_kde
scipy.stats.gaussian_kde
scipy.stats.gaussian_kde
--------------------
scipy.integrate.ode
--------------------
--------------------
--------------------
scipy.stats.sem
--------------------
--------------------
--------------------
scipy.stats.distributions.entropy
--------------------
scipy.stats.chisquare
scipy.stats.kstest
scipy.stats.kstest
scipy.stats.kstest
scipy.st

scipy.linalg.norm
scipy.linalg.norm
scipy.linalg.norm
scipy.linalg.norm
scipy.linalg.norm
scipy.linalg.eig
scipy.linalg.eig
scipy.linalg.inv
scipy.linalg.inv
scipy.linalg.norm
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.stats.mannwhitneyu
scipy.stats.mannwhitneyu
scipy.stats.mstats.kruskalwallis
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
scipy.stats.spearmanr
scipy.stats.pointbiserialr

In [54]:
for f in dp:
    if f not in func2vector:
        func2vector[f] = np.full((vector_size), 0.01)

In [55]:
idx2func = list(func2vector.keys())
func2idx = {f: i for i, f in enumerate(idx2func)}
vectors = [func2vector[f] for f in idx2func]
occur_matrix = np.stack(vectors)
cooccur_matrix = np.dot(occur_matrix, occur_matrix.T)

In [57]:
a = 1-cooccur_matrix/cooccur_matrix.max()

In [59]:
sim_mat = sklearn.metrics.pairwise.cosine_similarity(occur_matrix)

In [63]:
sorted_mat = np.argsort(sim_mat, axis = 1)

In [85]:
# find most similar functions 
# 备用，不影响整个流程
for i, s in enumerate(sorted_mat[:,-10:]):
    print('-'*20)
    for j in s[::-1]:
        if sim_mat[i,j]>=0.44:
            print(idx2func[j])

--------------------
sklearn.feature_extraction.text.TfidfVectorizer
--------------------
sklearn.feature_extraction.text.CountVectorizer
sklearn.naive_bayes.MultinomialNB
sklearn.feature_extraction.text.TfidfTransformer
--------------------
sklearn.linear_model.Log
--------------------
sklearn.svm.SVC
--------------------
sklearn.preprocessing.LabelEncoder
--------------------
sklearn.linear_model.Ridge
sklearn.linear_model.Lasso
--------------------
sklearn.metrics.classification_report
sklearn.metrics.confusion_matrix
--------------------
sklearn.linear_model.Lasso
sklearn.linear_model.Ridge
--------------------
sklearn.metrics.confusion_matrix
sklearn.metrics.classification_report
--------------------
sklearn.metrics.mean_squared_error
--------------------
sklearn.preprocessing.StandardScaler
--------------------
sklearn.neural_network.MLPClassifier
--------------------
sklearn.preprocessing.LabelBinarizer
--------------------
sklearn.cluster.spectral_clustering
sklearn.feature_ext

sklearn.linear_model.LassoLars
sklearn.linear_model.LassoCV
sklearn.linear_model.LarsCV
sklearn.linear_model.Hinge
--------------------
sklearn.preprocessing.quantile_transform
sklearn.linear_model.MultiTaskElasticNetCV
sklearn.linear_model.LogisticRegressionCV
sklearn.linear_model.LogisticRegression
sklearn.linear_model.LassoLarsIC
sklearn.linear_model.LassoLarsCV
sklearn.linear_model.LassoLars
sklearn.linear_model.LassoCV
sklearn.linear_model.LarsCV
sklearn.linear_model.Hinge
--------------------
sklearn.preprocessing.quantile_transform
sklearn.linear_model.MultiTaskElasticNetCV
sklearn.linear_model.LogisticRegressionCV
sklearn.linear_model.LogisticRegression
sklearn.linear_model.LassoLarsIC
sklearn.linear_model.LassoLarsCV
sklearn.linear_model.LassoLars
sklearn.linear_model.LassoCV
sklearn.linear_model.LarsCV
sklearn.linear_model.Hinge
--------------------
sklearn.preprocessing.quantile_transform
sklearn.linear_model.MultiTaskElasticNetCV
sklearn.linear_model.LogisticRegressionCV
sk

In [64]:
a = 1- sim_mat

In [66]:
model = cluster.AgglomerativeClustering(n_clusters = None, distance_threshold=0.8, affinity="precomputed", linkage="average").fit(a)





In [67]:
model.n_clusters_

80

In [68]:
clusters = {}
for i, l in enumerate(model.labels_):
    if l not in clusters:
        clusters[l] = []
    clusters[l].append(idx2func[i])
clusters = list(clusters.values())

In [70]:
for c in clusters:
    print('-'*20)
#     if 'sklearn.linear_model.Ridge' in c:
    for f in c:
        print(f)

--------------------
scipy.stats.rv_discrete
--------------------
scipy.stats.skew
scipy.stats.kurtosis
--------------------
scipy.optimize.brent
scipy.optimize.minimize
scipy.optimize.newton
scipy.optimize.root
scipy.optimize.fixed_point
scipy.optimize.rosen
--------------------
scipy.optimize.fmin
scipy.misc.face
scipy.linalg.det
scipy.optimize.fsolve
scipy.optimize.brute
scipy.optimize.basinhopping
scipy.stats.scoreatpercentile
--------------------
scipy.stats.probplot
--------------------
scipy.stats.chisquare
--------------------
scipy.stats.linregress
scipy.stats.spearmanr
--------------------
scipy.integrate.ode
--------------------
scipy.stats.mannwhitneyu
--------------------
scipy.integrate.quad
--------------------
scipy.stats.pearsonr
--------------------
scipy.sparse.diags
--------------------
scipy.sparse.hstack
scipy.sparse.csr_matrix
--------------------
scipy.stats.describe
--------------------
scipy.optimize.curve_fit
--------------------
scipy.stats.mode
------------